# Krafthack 2022 Baseline model

In [38]:
from ae_adx_client.ae_adx_client import AdxClient
import pandas as pd
import plotly.express as px
import numpy as np
from matplotlib import pyplot as plt
import os
from sklearn.linear_model import LinearRegression

In [ ]:
%load_ext autoreload
%autoreload 2

In [39]:
from data_helpers import get_operating_signal_names, get_tensile_sensor_names
from datetime import datetime as dt

In [40]:
start_date = dt(year=1970,month=9,day=11)
end_date = dt(year=1971,month=1,day=25)

steady_data = pd.read_parquet('../data/steady_data.parquet')
steady_data_for_linear_fit = steady_data.loc[start_date:end_date,get_tensile_sensor_names()]
steady_data_for_linear_fit = steady_data_for_linear_fit.resample('1s').interpolate()

unsteady_data = pd.read_parquet('../data/unsteady_data.parquet')

In [41]:
px.line(steady_data.loc[:,'Turbine_Pressure Spiral Casing'].sample(10000).sort_index())

In [42]:
steady_data_for_linear_fit['elapsed_time'] = steady_data_for_linear_fit.index-start_date
steady_data_for_linear_fit['elapsed_time'] = steady_data_for_linear_fit.elapsed_time / pd.to_timedelta(1,'s')
steady_data_for_linear_fit.head()

Bolt_1_Tensile  Bolt_2_Tensile  Bolt_3_Tensile  \
timepoints                                                            
1970-09-11 00:00:00     1474.110340     1427.721960     1623.672827   
1970-09-11 00:00:01     1474.178909     1427.745722     1623.634306   
1970-09-11 00:00:02     1474.125790     1427.762865     1623.654800   
1970-09-11 00:00:03     1474.042509     1427.678622     1623.572884   
1970-09-11 00:00:04     1474.137001     1427.774177     1623.649330   

                     Bolt_4_Tensile  Bolt_5_Tensile  Bolt_6_Tensile  \
timepoints                                                            
1970-09-11 00:00:00     1592.000401     1627.568274     1638.021667   
1970-09-11 00:00:01     1591.981665     1627.573384     1638.096755   
1970-09-11 00:00:02     1591.985490     1627.538896     1638.040184   
1970-09-11 00:00:03     1591.971247     1627.579170     1638.019175   
1970-09-11 00:00:04     1591.939368     1627.501739     1638.012018   

                     elapsed_time  
timepoints                         
1970-09-11 00:00:00           0.0  
1970-09-11 00:00:01           1.0  
1970-09-11 00:00:02           2.0  
1970-09-11 00:00:03           3.0  
1970-09-11 00:00:04           4.0

In [43]:
baseline_models = {}
for tensile_sensor in get_tensile_sensor_names():
    linear_model = LinearRegression()
    x = steady_data_for_linear_fit["elapsed_time"].values
    x = x.reshape(-1,1)
    y = steady_data_for_linear_fit[tensile_sensor].values
    y = y.reshape(-1,1)
    baseline_models[tensile_sensor] = linear_model.fit(
        X=x,
        y=y
    )


In [44]:
import pickle

with open('baseline_models.pkl','wb') as f:
    pickle.dump(baseline_models,f)

In [66]:
for tensile_sensor_name in get_tensile_sensor_names():
    linear_model = baseline_models.get(tensile_sensor_name)
    x_data = steady_data_for_linear_fit['elapsed_time'].values.reshape(-1,1)
    linear_prediction = linear_model.predict(X=x_data)
    plot_df = steady_data_for_linear_fit.loc[:,[tensile_sensor_name]]
    plot_df['linear_prediction'] = linear_prediction
    fig = px.line(plot_df.sample(10000).sort_index(),title=f"Baseline model for {tensile_sensor_name}")
    fig.show()
    

In [46]:
def detrend_tensile_data(df: pd.DataFrame,baseline_models: dict, start_date: dt, end_date: dt):
    """Detrend the tensile sensor data with model

    Args:
        df (pd.DataFrame): data with trends
        baseline_models (dict): dictionary with trained baseline models
    """
    df = df.copy()

    if 'elapsed_time' not in df.columns:
        
        df['elapsed_time'] = df.index-start_date
        df['elapsed_time'] = df.elapsed_time / pd.to_timedelta(1,'s')

    for tensile_sensor_name in get_tensile_sensor_names():

        x_data = df['elapsed_time'].values.reshape(-1,1)
        linear_model = baseline_models.get(tensile_sensor_name)
        df['trend'] = linear_model.predict(X=x_data)
        df.loc[:,tensile_sensor_name] = df[tensile_sensor_name]-df['trend']
        df.drop(columns=['trend'])
        df = df.loc[start_date:end_date,:]

    return df

In [47]:
detrended_steady_data = detrend_tensile_data(
    df=steady_data, 
    baseline_models=baseline_models,
    start_date=start_date,
    end_date=end_date
)



In [48]:
detrended_unsteady_data = detrend_tensile_data(
    df = unsteady_data,
    baseline_models=baseline_models,
    start_date=start_date,
    end_date=end_date
)

In [62]:
detrended_steady_data.head()

Unit_4_Power  Unit_4_Reactive Power  \
timepoints                                                 
1970-09-11 00:00:00    216.010229               2.213785   
1970-09-11 00:00:01    215.986387               2.430907   
1970-09-11 00:00:02    215.962544               2.648030   
1970-09-11 00:00:03    215.938701               2.865152   
1970-09-11 00:00:04    215.914859               3.082275   

                     Turbine_Guide Vane Opening  Turbine_Rotational Speed  \
timepoints                                                                  
1970-09-11 00:00:00                   72.927260                107.993752   
1970-09-11 00:00:01                   72.857113                107.993752   
1970-09-11 00:00:02                   72.786965                107.993752   
1970-09-11 00:00:03                   72.716817                107.993752   
1970-09-11 00:00:04                   72.646670                107.993752   

                     Turbine_Pressure Drafttube  \
timepoints                                        
1970-09-11 00:00:00                  152.625396   
1970-09-11 00:00:01                  152.426614   
1970-09-11 00:00:02                  152.221141   
1970-09-11 00:00:03                  152.015668   
1970-09-11 00:00:04                  151.810195   

                     Turbine_Pressure Spiral Casing  Bolt_1_Steel tmp  \
timepoints                                                              
1970-09-11 00:00:00                     5204.692439          9.116564   
1970-09-11 00:00:01                     5204.907020          9.116155   
1970-09-11 00:00:02                     5205.337213          9.117806   
1970-09-11 00:00:03                     5205.767405          9.117833   
1970-09-11 00:00:04                     5206.197597          9.117341   

                     Bolt_1_Torsion  Bolt_1_Tensile  Bolt_2_Torsion  ...  \
timepoints                                                           ...   
1970-09-11 00:00:00      161.624242        4.962772      132.720051  ...   
1970-09-11 00:00:01      161.641194        5.031327      132.716088  ...   
1970-09-11 00:00:02      161.646854        4.978194      132.706999  ...   
1970-09-11 00:00:03      161.632999        4.894897      132.720516  ...   
1970-09-11 00:00:04      161.632617        4.989375      132.704046  ...   

                     Bolt_4_Torsion  Bolt_4_Tensile  Bolt_5_Torsion  \
timepoints                                                            
1970-09-11 00:00:00      227.374230       -0.922153      286.245070   
1970-09-11 00:00:01      227.351792       -0.940889      286.227038   
1970-09-11 00:00:02      227.370264       -0.937066      286.243309   
1970-09-11 00:00:03      227.375600       -0.951310      286.247199   
1970-09-11 00:00:04      227.359891       -0.983190      286.232739   

                     Bolt_5_Tensile  Bolt_6_Torsion  Bolt_6_Tensile  \
timepoints                                                            
1970-09-11 00:00:00       -5.521569      166.092997       -3.766545   
1970-09-11 00:00:01       -5.516459      166.113711       -3.691460   
1970-09-11 00:00:02       -5.550948      166.106216       -3.748036   
1970-09-11 00:00:03       -5.510674      166.093641       -3.769048   
1970-09-11 00:00:04       -5.588106      166.102960       -3.776209   

                     lower_bearing_vib_vrt  turbine_bearing_vib_vrt  \
timepoints                                                            
1970-09-11 00:00:00                    NaN                      NaN   
1970-09-11 00:00:01                    NaN                      NaN   
1970-09-11 00:00:02                    NaN                      NaN   
1970-09-11 00:00:03                    NaN                      NaN   
1970-09-11 00:00:04                    NaN                      NaN   

                     elapsed_time        trend  
timepoints                                      
1970-09-11 00:00:00           0.0  1641.788212  
1970-09-11 00:00

In [51]:
training_columns = get_operating_signal_names() + get_tensile_sensor_names()
print(training_columns)
detrended_steady_data.loc[:,training_columns].dropna().head()

['Unit_4_Power', 'Unit_4_Reactive Power', 'Turbine_Guide Vane Opening', 'Turbine_Pressure Drafttube', 'Turbine_Pressure Spiral Casing', 'Turbine_Rotational Speed', 'Bolt_1_Tensile', 'Bolt_2_Tensile', 'Bolt_3_Tensile', 'Bolt_4_Tensile', 'Bolt_5_Tensile', 'Bolt_6_Tensile']


Unit_4_Power  Unit_4_Reactive Power  \
timepoints                                                 
1970-09-11 00:00:00    216.010229               2.213785   
1970-09-11 00:00:01    215.986387               2.430907   
1970-09-11 00:00:02    215.962544               2.648030   
1970-09-11 00:00:03    215.938701               2.865152   
1970-09-11 00:00:04    215.914859               3.082275   

                     Turbine_Guide Vane Opening  Turbine_Pressure Drafttube  \
timepoints                                                                    
1970-09-11 00:00:00                   72.927260                  152.625396   
1970-09-11 00:00:01                   72.857113                  152.426614   
1970-09-11 00:00:02                   72.786965                  152.221141   
1970-09-11 00:00:03                   72.716817                  152.015668   
1970-09-11 00:00:04                   72.646670                  151.810195   

                     Turbine_Pressure Spiral Casing  Turbine_Rotational Speed  \
timepoints                                                                      
1970-09-11 00:00:00                     5204.692439                107.993752   
1970-09-11 00:00:01                     5204.907020                107.993752   
1970-09-11 00:00:02                     5205.337213                107.993752   
1970-09-11 00:00:03                     5205.767405                107.993752   
1970-09-11 00:00:04                     5206.197597                107.993752   

                     Bolt_1_Tensile  Bolt_2_Tensile  Bolt_3_Tensile  \
timepoints                                                            
1970-09-11 00:00:00        4.962772       -7.615786       -2.839481   
1970-09-11 00:00:01        5.031327       -7.592030       -2.878009   
1970-09-11 00:00:02        4.978194       -7.574893       -2.857521   
1970-09-11 00:00:03        4.894897       -7.659141       -2.939444   
1970-09-11 00:00:04        4.989375       -7.563591       -2.863004   

                     Bolt_4_Tensile  Bolt_5_Tensile  Bolt_6_Tensile  
timepoints                                                           
1970-09-11 00:00:00       -0.922153       -5.521569       -3.766545  
1970-09-11 00:00:01       -0.940889       -5.516459       -3.691460  
1970-09-11 00:00:02       -0.937066       -5.550948       -3.748036  
1970-09-11 00:00:03       -0.951310       -5.510674       -3.769048  
1970-09-11 00:00:04       -0.983190       -5.588106       -3.776209

In [52]:
detrended_steady_data.loc[:,training_columns].dropna().to_parquet('../data/detrended_steady_data.parquet')
detrended_unsteady_data.loc[:,training_columns].dropna().to_parquet('../data/detrended_unsteady_data.parquet')

In [65]:
col = get_tensile_sensor_names()[0]

px.scatter(
    detrended_steady_data.sample(20000),
    x="Unit_4_Power",
    y=col,
    title=f"De-trended {col} values plottet against Active Power",
    height=800,
    width=800
)
